In [4]:
import time
from pymongo import MongoClient
from kafka3 import KafkaProducer
from bson.json_util import dumps

mongo_client = MongoClient("mongodb://172.27.65.143:27017")
db = mongo_client["fit3182_db"]
collection = db["Violations"]

producer = KafkaProducer(
    bootstrap_servers="172.17.0.1:9092",
    value_serializer=lambda v: dumps(v).encode('utf-8')
)

stream_topic = "mongo_plot_stream"

last_violation_timestamp = None

try:
    while True:
        all_docs = list(collection.find().sort("date", 1))
        for doc in all_docs:
            for violation in doc.get("violations", []):
                ts = violation.get("timestamp_start")
                print(ts)
                if last_violation_timestamp is None or ts > last_violation_timestamp:
                    producer.send(stream_topic, violation)
                    print(f"✅ Sent violation to Kafka: {violation}")
                    last_violation_timestamp = ts

        producer.flush()
        time.sleep(3)
except KeyboardInterrupt:
    print("Stopped by user")
finally:
    producer.close()


2024-01-01 08:21:05.725000
✅ Sent violation to Kafka: {'violation_id': '81e864ca-a187-467c-bceb-a9cb55e1368a', 'type': 'instantaneous', 'camera_id_start': 3, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 8, 21, 5, 725000), 'timestamp_end': None, 'measured_speed': 90.1}
2024-01-01 08:14:23.762000
2024-01-01 08:13:48.051000
2024-01-01 08:19:47
2024-01-01 08:20:15.304000
2024-01-01 08:19:47
2024-01-01 08:20:44.871000
2024-01-01 08:20:15.304000
2024-01-01 08:35:25
✅ Sent violation to Kafka: {'violation_id': 'eff86b75-0e9d-4f15-ac85-217e62d88c19', 'type': 'instantaneous', 'camera_id_start': 1, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 8, 35, 25), 'timestamp_end': None, 'measured_speed': 127.1}
2024-01-01 08:35:53.965000
✅ Sent violation to Kafka: {'violation_id': '95c21695-47ca-48ff-9c5e-8ffe72eda5be', 'type': 'instantaneous', 'camera_id_start': 2, 'camera_id_end': None, 'timestamp_start': datetime.datetime(2024, 1, 1, 8, 35, 53, 96500